- NO LIBRARIES

In [2]:
# Initialize an empty list to store the data from each file
data_list = []

# List of ARFF file names
arff_files = ['2017 Q1.arff',
'2017 Q2.arff',
'2017 Q3.arff',
'2017 Q4.arff',
'2017.arff',
'2018 Q1.arff',
'2018 Q2.arff',
'2018 Q3.arff',
'2018 Q4.arff',
'2018.arff',
'2019 Q1.arff',
'2019 Q2.arff',
'2019 Q3.arff',
'2019 Q4.arff',
'2019.arff',
'2020 Q1.arff',
'2020 Q2.arff',
'2020 Q3.arff',
'2020 Q4.arff',
'2020.arff',
'2021 Q1.arff'] 

# Read data from each ARFF file
for file_name in arff_files:
    with open(file_name, 'r') as file:
        lines = file.readlines()
        data_start = False
        current_data = []

        for line in lines:
            if data_start:
                # Assuming data lines start with '@data' and end with the end of the file
                current_data.append(line.strip().split(','))
            elif '@data' in line:
                data_start = True

        data_list.append(current_data)

# Combine data from all files into a single matrix
combined_matrix = [row for file_data in data_list for row in file_data]

# Print or use the combined matrix as needed
for row in combined_matrix:
    print(row)


['10', 'Hungary', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', '0', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', 'm', '1']
['22', 'Poland', '0', '0.49', '0.06', '1.31', '0.05', '0', '1.03', '0.17', '0.51', '0', '0.02', '0.03', '0', '0.01', '2.03', '0', '0.03', '0', '0', '0.46', '0', '0.21', '0.07', '6.21', '2.55', '0', '0.92', '0.34', '0', '0.17', '0.7', '0.82', '0', '0.66', '0', '-0.01', '1.2', '0.02', '0.14', '0.48', '0.18', '0.66', '1.07', '90336.59', '0', '0.62', '8.44', '1.69', '0.92', '0.22', '0.22', 'm', 'm', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0.01', '0', '0', '902.61', '105237.85', '20362.94', '942599.32', '457.4', '599.88', '1', '1', '1', '1', '1', '1', '1', '1'

In [9]:
def mean_center(data):
    # Compute the mean of each column and subtract it from the data
    num_samples = len(data)
    means = []

    for column in zip(*data):
        valid_entries = [entry for entry in column if entry is not None]
        column_mean = sum(valid_entries) / len(valid_entries) if valid_entries else 0
        means.append(column_mean)

    centered_data = [[entry - mean if entry is not None else None for entry, mean in zip(row, means)] for row in data]

    return centered_data, means

def cov_matrix(data):
    num_samples = len(data)
    num_features = len(data[0])

    cov_mat = [[0.0] * num_features for _ in range(num_features)]

    for i in range(num_features):
        for j in range(num_features):
            valid_entries = [data[k][i] * data[k][j] for k in range(num_samples) if data[k][i] is not None and data[k][j] is not None]
            cov_mat[i][j] = sum(valid_entries) / (num_samples - 1) if valid_entries else 0.0

    return cov_mat

def transpose(matrix):
    # Transpose a matrix
    return [[matrix[j][i] for j in range(len(matrix))] for i in range(len(matrix[0]))]

def matrix_multiply(matrix_a, matrix_b):
    num_rows_a, num_cols_a = len(matrix_a), len(matrix_a[0])
    num_rows_b, num_cols_b = len(matrix_b), len(matrix_b[0])

    # Check if the matrices can be multiplied
    if num_cols_a != num_rows_b:
        raise ValueError("Matrix dimensions are not compatible for multiplication")

    result = []

    for i in range(num_rows_a):
        row = []
        for j in range(num_cols_b):
            value = sum(matrix_a[i][k] * matrix_b[k][j] for k in range(num_cols_a))
            row.append(value)
        result.append(row)

    return result

# Function for power iteration to find the dominant eigenvalue and eigenvector
def power_iteration(matrix, num_iterations=1000):
    num_rows, num_cols = len(matrix), len(matrix[0])

    # Initialize a random vector as the starting point
    eigenvec = [1.0] * num_cols

    for _ in range(num_iterations):
        # Multiply the matrix with the current eigenvector
        temp = matrix_multiply(matrix, [eigenvec])
        temp = [v[0] for v in temp]

        # Normalize the eigenvector
        norm = max(abs(v) for v in temp)
        eigenvec = [v / norm for v in temp]

    # Compute the eigenvalue
    eigenvalue = sum(eigenvec[k] * temp[k] for k in range(num_cols))

    return eigenvalue, eigenvec


# Update the svd function to include eigenvalue decomposition
def svd(matrix):
    # Step 1: Compute eigenvalues and eigenvectors for A * A^T
    aat = matrix_multiply(matrix, transpose(matrix))
    print("A * A^T:")
    print(aat)
    eigenvalues_aat, eigenvectors_aat = power_iteration(aat)
    # Step 2: Compute eigenvalues and eigenvectors for A^T * A
    ata = matrix_multiply(transpose(matrix), matrix)
    print("A^T * A:")
    print(ata)

    eigenvalues_ata, eigenvectors_ata = power_iteration(ata)

    # Step 3: Compute singular values and right singular vectors
    # (Singular values are square roots of eigenvalues)
    singular_values = [eigenvalue**0.5 for eigenvalue in eigenvalues_ata]
    right_singular_vectors = eigenvectors_ata

    # Step 4: Compute left singular vectors using A * A^T
    left_singular_vectors = eigenvectors_aat

    return left_singular_vectors, singular_values, right_singular_vectors

def convert_to_float(value):
    try:
        if isinstance(value, str):
            return float(value) if value.replace('.', '', 1).isdigit() or (value[1:].replace('.', '', 1).isdigit() and value[0] == '-') else None
        elif isinstance(value, (int, float)):
            return float(value)
        else:
            return None
    except ValueError:
        return None

def pca(data, num_components):
    # Perform PCA on the data with the specified number of components
    centered_data, means = mean_center(data)
    cov_mat = cov_matrix(centered_data)
    eigenvectors, _ = svd(cov_mat)

    # Select the top 'num_components' eigenvectors
    principal_components = eigenvectors[:num_components]

    # Project the data onto the principal components
    pca_result = matrix_multiply(centered_data, transpose(principal_components))

    return pca_result

# Example usage:
# data is a 2D matrix where rows represent samples and columns represent features
# num_components is the number of principal components to retain
combined_matrix = [[convert_to_float(entry) for entry in row] for row in combined_matrix]
result = pca(combined_matrix, num_components=2)
print(result)

A * A^T:
[[2.1214908793565696e+16, 0.0, -1523887005969.2646, 7.888138657914659e+19, -8.572261016421146e+16, 92975028014659.45, 4.2806093689701473e+18, -150374091448092.56, 138053506520782.86, -7.899096903763426e+19, 1.7893687912029825e+20, -77212007815121.4, -99307630257332.03, -475693140422140.94, 429654007341.2816, -96624675424428.52, 297346372811441.1, -58029124279616.1, -506642183258132.1, -77800819296767.14, -193715294500796.25, 1.7465627012995324e+20, 6248294221012.038, 445590256147746.5, 62731807931730.56, 173172306365315.94, 4241909329689986.5, 1.031906035928265e+18, 273038465628731.97, 348192853529235.25, 386026382395146.9, -7.794920017041721e+19, 2177914084883423.2, 2.5695803435896186e+20, 44334396979510.42, 4791242175443448.0, -258903682927899.72, 73364423195901.62, 4877607062469694.0, -7.217659650155497e+18, -483608306890454.75, 153701772147084.5, 8.602311306414678e+17, -2551488960751.701, -14886003525153.111, 2.3296993751145236e+18, 1.9475984798081008e+17, -16914952379895.

ValueError: Matrix dimensions are not compatible for multiplication

- WITH LIBRARIES

In [5]:
import numpy as np
from sklearn.decomposition import PCA, TruncatedSVD
from sklearn.preprocessing import StandardScaler

def preprocess_data(combined_matrix):
    # Assuming combined_matrix is the data matrix
    data = np.array(combined_matrix)

    # Extract numerical features (excluding the second column)
    numerical_data = data[:, 0].astype(float)

    # Create a synthetic second feature with constant values
    second_feature = np.ones_like(numerical_data)

    # Stack the features horizontally
    combined_features = np.column_stack((numerical_data, second_feature))

    return combined_features

def apply_pca(data, n_components=1):
    # Standardize data
    scaler = StandardScaler()
    standardized_data = scaler.fit_transform(data)

    # Perform PCA with scikit-learn
    pca = PCA(n_components=n_components)
    pca_transformed_data = pca.fit_transform(standardized_data)

    return pca, pca_transformed_data

def apply_truncated_svd(data, n_components=1):
    # Standardize data
    scaler = StandardScaler()
    standardized_data = scaler.fit_transform(data)

    # Perform Truncated SVD with scikit-learn
    svd = TruncatedSVD(n_components=n_components)
    svd_transformed_data = svd.fit_transform(standardized_data)

    return svd, svd_transformed_data

def print_results(method_name, decomposition, transformed_data):
    print(f"\nExplained Variance Ratio ({method_name}):", decomposition.explained_variance_ratio_.tolist())
    print(f"{method_name} Transformed Data:")
    print(transformed_data.tolist())

# Example Usage:
combined_matrix = [[convert_to_float(entry) for entry in row] for row in combined_matrix]

# Preprocess data
processed_data = preprocess_data(combined_matrix)

# Apply PCA
pca, pca_transformed_data = apply_pca(processed_data, n_components=1)
print_results("PCA", pca, pca_transformed_data)

# Apply Truncated SVD
svd, svd_transformed_data = apply_truncated_svd(processed_data, n_components=1)
print_results("Truncated SVD", svd, svd_transformed_data)



Explained Variance Ratio (PCA): [1.0000000000000027]
PCA Transformed Data:
[[-1.6589238695848936], [-1.566547598424722], [-1.5280574854413125], [-1.1739484459939555], [-1.1662504233972737], [-0.9661018358835503], [-0.6658789546129649], [-0.6427848868229199], [-0.3887501411324245], [-0.06543319207179421], [0.24248771179547277], [0.3425620055523346], [0.3887501411324246], [0.49652245748596807], [1.0815721748337752], [1.3817950561043608], [1.4587752820711775], [-1.6435278243915379], [-1.589641666214766], [-1.5742456210214024], [-1.5126614402479492], [-1.5049634176512676], [-1.4048891238944057], [-1.3894930787010424], [-1.2509286719607722], [-1.2124385589773639], [-1.1277603104138654], [-1.066176129640412], [-1.043082061850367], [-1.0045919488669586], [-0.9891959036735951], [-0.9507057906901869], [-0.8968196325134151], [-0.8891216099167335], [-0.8352354517399617], [-0.7197651127897365], [-0.6042947738395115], [-0.5504086156627398], [-0.43493827671251456], [-0.38105211853574283], [-0.26558

### Conclusion

Differences contributing to potential discrepancies between the two codes include variations in data preprocessing, specifically standardization; the code that utilizes Python libraries standardizes data using StandardScaler, impacting data scale and PCA results, while the manual code solely mean centers the data. Furthermore, divergent implementation details play a role, with the second code utilizing scikit-learn's optimized PCA and Truncated SVD implementations, while the first code manually computes the covariance matrix, eigenvalues, and eigenvectors. These distinct approaches may introduce numerical differences. Additionally, differences in output format exist as the second code prints the explained variance ratio, offering insights into the significance of retained variance by each principal component, while the first code lacks this information, hindering a comprehensive assessment of feature retention during dimensionality reduction. 